In [1]:
import numpy as np
import pandas as pd
import folium as fm
import json

In [2]:
volcano_map=fm.Map(max_bounds=True,min_zoom=2)
us_cities_map=fm.Map(location=[39.5,-98.35],max_bounds=True,min_zoom=4,zoom_start=4)
us_states_map=fm.Map(location=[39.5,-98.35],max_bounds=True,min_zoom=4,zoom_start=4)

In [3]:
volcanos=pd.read_csv('./volcano.csv')
volcanos.head()

Year  Month   Day  TSU   EQ                    Name              Location  \
0  2010      1   NaN  NaN  NaN              Tungurahua               Ecuador   
1  2010      3  31.0  NaN  NaN        Eyjafjallajokull             Iceland-S   
2  2010      5  27.0  NaN  NaN                  Pacaya             Guatemala   
3  2010      5  29.0  TSU   EQ                 Sarigan  Mariana Is-C Pacific   
4  2010      8   6.0  NaN  NaN  Karangetang [Api Siau]  Sangihe Is-Indonesia   

         Country  Latitude  Longitude  ...  TOTAL_DEATHS  \
0        Ecuador    -1.467    -78.442  ...           NaN   
1        Iceland    63.630    -19.620  ...           2.0   
2      Guatemala    14.381    -90.601  ...           1.0   
3  United States    16.708    145.780  ...           NaN   
4      Indonesia     2.780    125.480  ...           4.0   

  TOTAL_DEATHS_DESCRIPTION TOTAL_MISSING TOTAL_MISSING_DESCRIPTION  \
0                      NaN           NaN                       NaN   
1                      1.0           NaN                       NaN   
2                      1.0           3.0                       1.0   
3                      NaN           NaN                       NaN   
4                      1.0           NaN                       NaN   

   TOTAL_INJURIES TOTAL_INJURIES_DESCRIPTION  TOTAL_DAMAGE_MILLIONS_DOLLARS  \
0             NaN                        NaN                            NaN   
1             NaN                        NaN                            NaN   
2             NaN                        NaN                            NaN   
3             NaN                        NaN                            NaN   
4             5.0                        1.0                            NaN   

   TOTAL_DAMAGE_DESCRIPTION  TOTAL_HOUSES_DESTROYED  \
0                       1.0                     NaN   
1                       NaN                     NaN   
2                       1.0                     3.0   
3                       NaN                     NaN   
4                       NaN                     NaN   

   TOTAL_HOUSES_DESTROYED_DESCRIPTION  
0                                 NaN  
1                                 NaN  
2                                 1.0  
3                                 NaN  
4                                 1.0  

[5 rows x 36 columns]

In [4]:
volcanos_markers=fm.FeatureGroup()
for index, row in volcanos.iterrows():
    volcanos_markers.add_child(
        fm.Marker(
            location=[row['Latitude'],row['Longitude']],
            tooltip=fm.Tooltip(f"{row['Name']}, {row['Country']}"),
            icon=fm.Icon(color='red',icon='warning-sign')
        )
    )
    
volcano_map.add_child(volcanos_markers)

In [5]:
us_cities_population=pd.read_csv('./US_Population_cities_2019.csv')

max_pop=us_cities_population['pop'].max()
min_pop=us_cities_population['pop'].min()

us_cities_population['relative_pop']=(us_cities_population['pop']-min_pop)/max_pop

us_cities_population['rank_pop']=us_cities_population['pop'].rank(pct=True)

def color_set(value):
    if value<=.25:
        return 'red'

    elif value<=.75:
        return'blue'
    
    else :
        return 'green'

us_cities_population['color']=us_cities_population['rank_pop'].apply(color_set)

us_cities_population.head()



name      pop        lat         lon  relative_pop  rank_pop  \
0      New York   8287238  40.730599  -73.986581      0.999144  1.000000   
1   Los Angeles   3826423  34.053717 -118.242727      0.460869  0.999690   
2       Chicago   2705627  41.875555  -87.624421      0.325625  0.999380   
3       Houston   2129784  29.758938  -95.367697      0.256140  0.999071   
4  Philadelphia   1539313  39.952335  -75.163789      0.184889  0.998761   

   color  
0  green  
1  green  
2  green  
3  green  
4  green

In [6]:
us_markers=fm.FeatureGroup()

for (index,city) in us_cities_population.iterrows():
    us_markers.add_child(
        fm.CircleMarker(
            location=[city['lat'],city['lon']],
            tooltip=fm.Tooltip(f"{city['name']}, {city['pop']}"),
            radius=city['relative_pop']*100,
            fill=True,
            opacity=0.8,
            color=city['color']
        )
    )

us_cities_map.add_child(us_markers)

In [7]:
us_states_population=pd.read_csv('./US_Population_states_2019.csv',index_col='state')

us_states_population['rank_pop']=us_states_population['population'].rank(pct=True)

us_states_population['color']=us_states_population['rank_pop'].apply(color_set)

us_states_population.head()

population        lat        long  rank_pop  color
state                                                         
Alabama        4903185  32.377716  -86.300568  0.549020   blue
Alaska          731545  58.301598 -134.420212  0.078431    red
Arizona        7278717  33.448143 -112.096962  0.745098   blue
Arkansas       3017804  34.746613  -92.288986  0.372549   blue
California    39512223  38.576668 -121.493629  1.000000  green

In [10]:
with open('./us_map.json','r',encoding='utf-8-sig') as file :
    geojson_states=json.load(file)


for state in geojson_states['features']:
    name=state['properties']['name']
    state['properties']['population']=f"{us_states_population.loc[name]['population']:,}"

In [11]:
us_states_map.add_child(
    fm.GeoJson(
        data=geojson_states,
        style_function = lambda feature: {'color': us_states_population.loc[feature['properties']['name']]['color']},
        tooltip=fm.GeoJsonTooltip(
                fields=['name','population'],
                aliases=['State: ','Population: ']
                ),
        )
    )
